In [1]:
import tensorflow as tf
# #指定使用那块GUP训练
import os

os.environ["CUDA_VISIBLE_DEVICES"] = "0"
config = tf.ConfigProto()
# 设置最大占有GPU不超过显存的70%
config.gpu_options.per_process_gpu_memory_fraction = 0.7 
# # 重点：设置动态分配GPU
config.gpu_options.allow_growth = True
# 创建session时
tf.Session(config=config) 

In [ ]:
import numpy as np
from keras.datasets import cifar10
from torch.utils.data import Dataset
import torch.utils.data as Data
class MyDataset(Dataset):
    def __init__(self, imgs, transform=None):
        # super().__init__()
        self.imgs = imgs
        self.transform = transform

    def __len__(self):
        return len(self.imgs)

    def __getitem__(self, index):
        img = self.imgs[index]
        if self.transform is not None:
            img = self.transform(img)
        else:
            img = torch.from_numpy(img)
        img=img.reshape([3,32,32])
        return img
import torch
from torch.autograd import Variable
import model
import torch.nn.functional as F
model = model.cifar10(128)
model.load_state_dict(torch.load('./log/default/best-85.pth'))
model.cuda()
def get_mean_var(y_logit):
    y_logit=np.abs(y_logit-0.1)
    return np.mean(y_logit,axis=1)

def get_possibility(images):
    x_dataset = MyDataset(images)
    # print(x_dataset[0].shape)
    x_real_loader = Data.DataLoader(dataset=x_dataset, batch_size=100, shuffle=True)
    y_logits = []
    for i, data in enumerate(x_real_loader):
        # indx_target = target.clone()
        data = data.cuda()
        data = Variable(data, volatile=True)
        output = model(data)
        pred = F.softmax(output).cpu().detach().numpy()
        y_logits += [i for i in pred]
        y_logits=np.array(y_logits)
    return y_logits
import os
if not os.path.isdir('saved_models_{}'.format('wpgan')):
    os.mkdir('saved_models_{}'.format('wpgan'))
f = open('saved_models_{}/log_collapse1.txt'.format('wpgan'), mode='w')
import torch.utils.data as Data
import cv2

# Large amount of credit goes to:
# https://github.com/keras-team/keras-contrib/blob/master/examples/improved_wgan.py
# which I've used as a reference for this implementation
from keras.datasets import cifar10
from keras.layers.merge import _Merge
from keras.layers import Input, Dense, Reshape, Flatten, Dropout
from keras.layers import BatchNormalization, Activation, ZeroPadding2D
from keras.layers.advanced_activations import LeakyReLU
from keras.layers.convolutional import UpSampling2D, Conv2D
from keras.models import Sequential, Model
from keras.optimizers import RMSprop
from functools import partial
from PIL import Image
import keras.backend as K

import matplotlib.pyplot as plt

import sys

import numpy as np
import os
class RandomWeightedAverage(_Merge):
    """Provides a (random) weighted average between real and generated image samples"""
    def _merge_function(self, inputs):
        alpha = K.random_uniform((32, 1, 1, 1))
        return (alpha * inputs[0]) + ((1 - alpha) * inputs[1])

class WGANGP():
    def __init__(self):
        self.img_rows = 32
        self.img_cols = 32
        self.channels = 3
        self.img_shape = (self.img_rows, self.img_cols, self.channels)
        self.latent_dim = 100
        self.x = []
        self.y = np.zeros((31, 1), dtype=np.int)
        self.y = list(self.y)
        for i in range(31):
            self.y[i] = []

        # Following parameter and optimizer set as recommended in paper
        self.n_critic = 5
        optimizer = RMSprop(lr=0.00005)

        # Build the generator and critic
        self.generator = self.build_generator()
        self.critic = self.build_critic()

        #-------------------------------
        # Construct Computational Graph
        #       for the Critic
        #-------------------------------

        # Freeze generator's layers while training critic
        self.generator.trainable = False

        # Image input (real sample)
        real_img = Input(shape=self.img_shape)

        # Noise input
        z_disc = Input(shape=(self.latent_dim,))
        # Generate image based of noise (fake sample)
        fake_img = self.generator(z_disc)

        # Discriminator determines validity of the real and fake images
        fake = self.critic(fake_img)
        valid = self.critic(real_img)

        # Construct weighted average between real and fake images
        interpolated_img = RandomWeightedAverage()([real_img, fake_img])
        # Determine validity of weighted sample
        validity_interpolated = self.critic(interpolated_img)

        # Use Python partial to provide loss function with additional
        # 'averaged_samples' argument
        partial_gp_loss = partial(self.gradient_penalty_loss,
                          averaged_samples=interpolated_img)
        partial_gp_loss.__name__ = 'gradient_penalty' # Keras requires function names

        self.critic_model = Model(inputs=[real_img, z_disc],
                            outputs=[valid, fake, validity_interpolated])
        self.critic_model.compile(loss=[self.wasserstein_loss,
                                              self.wasserstein_loss,
                                              partial_gp_loss],
                                        optimizer=optimizer,
                                        loss_weights=[1, 1, 10])
        #-------------------------------
        # Construct Computational Graph
        #         for Generator
        #-------------------------------

        # For the generator we freeze the critic's layers
        self.critic.trainable = False
        self.generator.trainable = True

        # Sampled noise for input to generator
        z_gen = Input(shape=(100,))
        # Generate images based of noise
        img = self.generator(z_gen)
        # Discriminator determines validity
        valid = self.critic(img)
        # Defines generator model
        self.generator_model = Model(z_gen, valid)
        self.generator_model.compile(loss=self.wasserstein_loss, optimizer=optimizer)


    def gradient_penalty_loss(self, y_true, y_pred, averaged_samples):
        """
        Computes gradient penalty based on prediction and weighted real / fake samples
        """
        gradients = K.gradients(y_pred, averaged_samples)[0]
        # compute the euclidean norm by squaring ...
        gradients_sqr = K.square(gradients)
        #   ... summing over the rows ...
        gradients_sqr_sum = K.sum(gradients_sqr,
                                  axis=np.arange(1, len(gradients_sqr.shape)))
        #   ... and sqrt
        gradient_l2_norm = K.sqrt(gradients_sqr_sum)
        # compute lambda * (1 - ||grad||)^2 still for each single sample
        gradient_penalty = K.square(1 - gradient_l2_norm)
        # return the mean as loss over all the batch samples
        return K.mean(gradient_penalty)


    def wasserstein_loss(self, y_true, y_pred):
        return K.mean(y_true * y_pred)

    def build_generator(self):

        model = Sequential()

        model.add(Dense(128 * 8 * 8, activation="relu", input_dim=self.latent_dim))
        model.add(Reshape((8, 8, 128)))
        model.add(UpSampling2D())
        model.add(Conv2D(128, kernel_size=4, padding="same"))
        model.add(BatchNormalization(momentum=0.8))
        model.add(Activation("relu"))
        model.add(UpSampling2D())
        model.add(Conv2D(64, kernel_size=4, padding="same"))
        model.add(BatchNormalization(momentum=0.8))
        model.add(Activation("relu"))
        model.add(Conv2D(self.channels, kernel_size=4, padding="same"))
        model.add(Activation("tanh"))

        model.summary()

        noise = Input(shape=(self.latent_dim,))
        img = model(noise)

        return Model(noise, img)

    def build_critic(self):

        model = Sequential()

        model.add(Conv2D(16, kernel_size=3, strides=2, input_shape=self.img_shape, padding="same"))
        model.add(LeakyReLU(alpha=0.2))
        model.add(Dropout(0.25))
        model.add(Conv2D(32, kernel_size=3, strides=2, padding="same"))
        # model.add(ZeroPadding2D(padding=((0,1),(0,1))))
        model.add(BatchNormalization(momentum=0.8))
        model.add(LeakyReLU(alpha=0.2))
        model.add(Dropout(0.25))
        model.add(Conv2D(64, kernel_size=3, strides=2, padding="same"))
        model.add(BatchNormalization(momentum=0.8))
        model.add(LeakyReLU(alpha=0.2))
        model.add(Dropout(0.25))
        model.add(Conv2D(128, kernel_size=3, strides=1, padding="same"))
        model.add(BatchNormalization(momentum=0.8))
        model.add(LeakyReLU(alpha=0.2))
        model.add(Dropout(0.25))
        model.add(Flatten())
        model.add(Dense(1))

        model.summary()

        img = Input(shape=self.img_shape)
        validity = model(img)

        return Model(img, validity)

    def train(self, epochs, batch_size, sample_interval=50):

        # Load the dataset
        (X_train, _), (X_test, _) = cifar10.load_data()

        # Rescale -1 to 1
        X_train = (X_train.astype(np.float32) - 127.5) / 127.5
        X_test = (X_test.astype(np.float32) - 127.5) / 127.5
        # X_train = np.expand_dims(X_train, axis=3)

        # Adversarial ground truths
        valid = -np.ones((batch_size, 1))
        fake =  np.ones((batch_size, 1))
        dummy = np.zeros((batch_size, 1)) # Dummy gt for gradient penalty
        nb_batches = int(X_train.shape[0] / batch_size)
        global_step = 0
        steps = []
        values = []

        for epoch in range(epochs):

            for index in range(nb_batches):
                for _ in range(self.n_critic):
                    global_step += 1
                    imgs = X_train[index * batch_size:(index + 1) * batch_size]
                    # Sample generator input
                    noise = np.random.normal(0, 1, (batch_size, self.latent_dim))
                    # Train the critic
                    d_loss = self.critic_model.train_on_batch([imgs, noise],
                                                              [valid, fake, dummy])

                    # ---------------------
                    #  Train Generator
                    # ---------------------

                g_loss = self.generator_model.train_on_batch(noise, valid)

                # Plot the progress
                print("epoch%d step%d [D loss: %f] [G loss: %f]" % (epoch, global_step, d_loss[0], g_loss))

                if global_step % sample_interval == 0:
                    self.mode_drop(epoch, global_step)
                    

    def mode_drop(self, epoch, global_step):
        r, c = 10, 1000
        noise = np.random.normal(0, 1, (r * c, 100))
        # sampled_labels = np.array([num for _ in range(r) for num in range(c)])
        gen_imgs = self.generator.predict([noise])
        # Rescale images 0 - 1
        gen_imgs = 0.5 * gen_imgs + 0.5
        y_logits = get_possibility(gen_imgs)
        metrics = get_mean_var(y_logits)


        f.writelines('\n')
        f.writelines('global_step:' + str(global_step))
        f.writelines('\n')
        f.writelines(' %.8f ' % (i) for i in metrics)
        f.writelines('\n')
if __name__ == '__main__':
    wgan = WGANGP()
    wgan.train(epochs=50, batch_size=32, sample_interval=200)


Using TensorFlow backend.
Sequential(
  (0): Conv2d(3, 128, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
  (1): BatchNorm2d(128, eps=1e-05, momentum=0.1, affine=False, track_running_stats=True)
  (2): ReLU()
  (3): Conv2d(128, 128, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
  (4): BatchNorm2d(128, eps=1e-05, momentum=0.1, affine=False, track_running_stats=True)
  (5): ReLU()
  (6): MaxPool2d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
  (7): Conv2d(128, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
  (8): BatchNorm2d(256, eps=1e-05, momentum=0.1, affine=False, track_running_stats=True)
  (9): ReLU()
  (10): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
  (11): BatchNorm2d(256, eps=1e-05, momentum=0.1, affine=False, track_running_stats=True)
  (12): ReLU()
  (13): MaxPool2d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
  (14): Conv2d(256, 512, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
  (15): 

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_1 (Dense)              (None, 8192)              827392    
_________________________________________________________________
reshape_1 (Reshape)          (None, 8, 8, 128)         0         
_________________________________________________________________
up_sampling2d_1 (UpSampling2 (None, 16, 16, 128)       0         
_________________________________________________________________
conv2d_1 (Conv2D)            (None, 16, 16, 128)       262272    
_________________________________________________________________
batch_normalization_1 (Batch (None, 16, 16, 128)       512       
_________________________________________________________________
activation_1 (Activation)    (None, 16, 16, 128)       0         
_________________________________________________________________
up_sampling2d_2 (UpSampling2 (None, 32, 32, 128)       0         
__________

/home/imi432_006/anaconda3/envs/tf/lib/python3.5/site-packages/keras/engine/training.py:490: UserWarning: Discrepancy between trainable weights and collected trainable weights, did you set `model.trainable` without calling `model.compile` after ?
  'Discrepancy between trainable weights and collected trainable'


epoch0 step5 [D loss: 44.297760] [G loss: -0.259129]
epoch0 step10 [D loss: 33.561253] [G loss: -0.350380]
epoch0 step15 [D loss: 36.123478] [G loss: 0.005801]
epoch0 step20 [D loss: 27.202267] [G loss: -0.391423]
epoch0 step25 [D loss: 28.760288] [G loss: -0.042277]
epoch0 step30 [D loss: 27.379728] [G loss: -0.282992]
epoch0 step35 [D loss: 15.938297] [G loss: -0.265241]
epoch0 step40 [D loss: 18.647179] [G loss: -0.124318]
epoch0 step45 [D loss: 17.716377] [G loss: -0.139626]
epoch0 step50 [D loss: 13.436038] [G loss: -0.408755]
epoch0 step55 [D loss: 17.429522] [G loss: -0.081152]
epoch0 step60 [D loss: 8.413669] [G loss: -0.420968]
epoch0 step65 [D loss: 10.219528] [G loss: -0.167775]
epoch0 step70 [D loss: 7.795010] [G loss: -0.270853]
epoch0 step75 [D loss: 7.244645] [G loss: -0.156386]
epoch0 step80 [D loss: 6.199377] [G loss: -0.087434]
epoch0 step85 [D loss: 6.448745] [G loss: 0.007839]
epoch0 step90 [D loss: 6.714252] [G loss: 0.094889]
epoch0 step95 [D loss: 3.794759] [G lo

/home/imi432_006/anaconda3/envs/tf/lib/python3.5/site-packages/ipykernel_launcher.py:41: UserWarning: volatile was removed and now has no effect. Use `with torch.no_grad():` instead.
/home/imi432_006/anaconda3/envs/tf/lib/python3.5/site-packages/ipykernel_launcher.py:43: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.


...

epoch48 step382245 [D loss: -0.731308] [G loss: -1.796052]
epoch48 step382250 [D loss: 0.486979] [G loss: -1.854696]
epoch48 step382255 [D loss: -0.153919] [G loss: -1.997204]
epoch48 step382260 [D loss: -0.499145] [G loss: -1.629624]
epoch48 step382265 [D loss: 0.431033] [G loss: -2.093188]
epoch48 step382270 [D loss: 0.462222] [G loss: -2.212146]
epoch48 step382275 [D loss: -0.029125] [G loss: -2.509149]
epoch48 step382280 [D loss: 0.063965] [G loss: -1.832755]
epoch48 step382285 [D loss: 0.420406] [G loss: -2.234336]
epoch48 step382290 [D loss: -0.231357] [G loss: -2.032374]
epoch48 step382295 [D loss: 0.155353] [G loss: -1.983411]
epoch48 step382300 [D loss: -0.388742] [G loss: -1.965894]
epoch48 step382305 [D loss: 0.223501] [G loss: -2.089577]
epoch48 step382310 [D loss: 0.137302] [G loss: -2.193264]
epoch48 step382315 [D loss: 0.151264] [G loss: -1.820100]
epoch48 step382320 [D loss: 0.044651] [G loss: -1.683292]
epoch48 step382325 [D loss: -0.261967] [G loss: -1.946858]
epoch48

epoch49 step382945 [D loss: -0.679985] [G loss: -2.317442]
epoch49 step382950 [D loss: 0.225302] [G loss: -1.819007]
epoch49 step382955 [D loss: -0.194827] [G loss: -2.247550]
epoch49 step382960 [D loss: -0.457989] [G loss: -1.909094]
epoch49 step382965 [D loss: 0.486584] [G loss: -2.179765]
epoch49 step382970 [D loss: 0.152445] [G loss: -1.913384]
epoch49 step382975 [D loss: 0.019094] [G loss: -2.523111]
epoch49 step382980 [D loss: -0.500997] [G loss: -1.815285]
epoch49 step382985 [D loss: -0.139076] [G loss: -1.771311]
epoch49 step382990 [D loss: -0.461155] [G loss: -1.932002]
epoch49 step382995 [D loss: -0.284811] [G loss: -1.631314]
epoch49 step383000 [D loss: 0.182264] [G loss: -1.672539]
epoch49 step383005 [D loss: 0.162356] [G loss: -1.694237]
epoch49 step383010 [D loss: -0.115860] [G loss: -1.894325]
epoch49 step383015 [D loss: -0.559459] [G loss: -2.043538]
epoch49 step383020 [D loss: 0.053877] [G loss: -1.447359]
epoch49 step383025 [D loss: -0.820265] [G loss: -1.610901]
epoc

epoch49 step383655 [D loss: -0.267545] [G loss: -1.211895]
epoch49 step383660 [D loss: -0.026368] [G loss: -1.318393]
epoch49 step383665 [D loss: -0.239532] [G loss: -1.726274]
epoch49 step383670 [D loss: -0.073139] [G loss: -1.139931]
epoch49 step383675 [D loss: 0.301799] [G loss: -1.169646]
epoch49 step383680 [D loss: -0.373862] [G loss: -1.626910]
epoch49 step383685 [D loss: -0.041739] [G loss: -0.834070]
epoch49 step383690 [D loss: -0.517982] [G loss: -1.309765]
epoch49 step383695 [D loss: -0.509848] [G loss: -1.187292]
epoch49 step383700 [D loss: -0.298703] [G loss: -1.506652]
epoch49 step383705 [D loss: -0.709133] [G loss: -1.485873]
epoch49 step383710 [D loss: -0.488365] [G loss: -1.410948]
epoch49 step383715 [D loss: -0.063404] [G loss: -1.480023]
epoch49 step383720 [D loss: -0.600009] [G loss: -1.265960]
epoch49 step383725 [D loss: -0.290004] [G loss: -1.266951]
epoch49 step383730 [D loss: -0.249983] [G loss: -0.990306]
epoch49 step383735 [D loss: 0.254665] [G loss: -1.281268]

epoch49 step384355 [D loss: -1.050668] [G loss: -1.390340]
epoch49 step384360 [D loss: -0.071970] [G loss: -1.492847]
epoch49 step384365 [D loss: 0.397572] [G loss: -1.846307]
epoch49 step384370 [D loss: -0.192343] [G loss: -1.681828]
epoch49 step384375 [D loss: -0.811354] [G loss: -1.847490]
epoch49 step384380 [D loss: -0.161917] [G loss: -2.182185]
epoch49 step384385 [D loss: 0.380428] [G loss: -1.867048]
epoch49 step384390 [D loss: 0.409919] [G loss: -2.074400]
epoch49 step384395 [D loss: -0.322063] [G loss: -2.516195]
epoch49 step384400 [D loss: -0.013377] [G loss: -2.386209]
epoch49 step384405 [D loss: -0.466065] [G loss: -1.871973]
epoch49 step384410 [D loss: -0.186574] [G loss: -1.976166]
epoch49 step384415 [D loss: -0.067877] [G loss: -2.188511]
epoch49 step384420 [D loss: -0.272447] [G loss: -1.646016]
epoch49 step384425 [D loss: -0.383216] [G loss: -1.282948]
epoch49 step384430 [D loss: 0.231781] [G loss: -2.006042]
epoch49 step384435 [D loss: 0.264126] [G loss: -1.768988]
ep

epoch49 step385055 [D loss: -0.535818] [G loss: -1.665915]
epoch49 step385060 [D loss: 0.349339] [G loss: -2.038239]
epoch49 step385065 [D loss: -0.378471] [G loss: -2.096092]
epoch49 step385070 [D loss: 0.504457] [G loss: -2.424245]
epoch49 step385075 [D loss: -0.361149] [G loss: -1.652035]
epoch49 step385080 [D loss: -0.182859] [G loss: -1.722141]
epoch49 step385085 [D loss: 0.529907] [G loss: -1.890209]
epoch49 step385090 [D loss: -0.064746] [G loss: -2.086669]
epoch49 step385095 [D loss: -0.035683] [G loss: -2.293459]
epoch49 step385100 [D loss: -0.355148] [G loss: -1.444825]
epoch49 step385105 [D loss: 0.254504] [G loss: -1.523721]
epoch49 step385110 [D loss: -0.048838] [G loss: -2.050899]
epoch49 step385115 [D loss: 0.216605] [G loss: -2.222450]
epoch49 step385120 [D loss: -0.076967] [G loss: -1.818195]
epoch49 step385125 [D loss: 0.399039] [G loss: -2.111453]
epoch49 step385130 [D loss: -0.368417] [G loss: -1.725497]
epoch49 step385135 [D loss: -0.893106] [G loss: -2.427032]
epo